In [ ]:
pip install git+http://github.com/yhilpisch/tpqoa

  Cloning http://github.com/yhilpisch/tpqoa to /tmp/pip-req-build-qkbwi06z
  Running command git clone --filter=blob:none --quiet http://github.com/yhilpisch/tpqoa /tmp/pip-req-build-qkbwi06z
  Resolved http://github.com/yhilpisch/tpqoa to commit 4a79f30b7095642844ef99741d9bfcb952e394db
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.1/75.1 kB 2.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.9/53.9 kB 6.2 MB/s eta 0:00:00
  Created wheel for tpqoa: filename=tpqoa-0.0.56-py3-none-any.whl size=11593 sha256=eb82c63894b1a0b46c577f47808a558fb812e78be635dec3edb2e6d128454362
  Stored in directory: /tmp/pip-ephem-wheel-cache-kidod20r/wheels/64/6a/c3/9ac67ff8c56db797a1f480e0a121b221493f16fed4d517013d
  Created wheel for v20: filename=v20-3.0.25.0-py3-none-any.whl size=85779 sha256=4c6efd77dc7e96f8452dabd32e0568def088a700d1f3eef0d1480b3ed20f2ddf
  Stored in directory: /root/.cache/pip/wheels/b

In [ ]:
pip install vectorbt

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 526.7/526.7 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 13.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 8.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.5/3.5 MB 16.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.6/34.6 MB 33.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 31.3 MB/s eta 0:00:00
  Attempting uninstall: llvmlite
    Found existing installation: llvmlite 0.41.1
    Uninstalling llvmlite-0.41.1:
      Successfully uninstalled llvmlite-0.41.1
  Attempting uninstall: numba
    Found existing installation: numba 0.58.1
    Uninstalling numba-0.58.1:
      Successfully uninstalled numba-0.58.1


In [ ]:
pip install ta

  Preparing metadata (setup.py) ... done
  Created wheel for ta: filename=ta-0.11.0-py3-none-any.whl size=29413 sha256=18c28e60f04fc9a855b0047183492e1be870e89454157eaed62ba9e94919634f
  Stored in directory: /root/.cache/pip/wheels/5f/67/4f/8a9f252836e053e532c6587a3230bc72a4deb16b03a829610b
Successfully built ta


In [ ]:
pip install q

In [ ]:
import numpy as np
import pandas as pd
from pylab import plt
import tpqoa
import vectorbt as vbt
import ta
import q
from ta.volatility import BollingerBands
from sklearn.model_selection import TimeSeriesSplit
from sklearn.ensemble import BaggingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import cross_validate
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import GridSearchCV
from xgboost import XGBClassifier

In [ ]:
class AlgoTrader(tpqoa.tpqoa):
    def __init__(self, config_file, instrument="EUR_USD", granularity='M1',
                 train_start='2023-11-10', train_end='2023-11-24',
                 test_start='2023-11-25', test_end='2023-12-05', price='M', trading_units=1000, features=[], lags=20, FeatWindow=20):
        super(AlgoTrader, self).__init__(config_file)

        # initialise parameters for model fitting and backtesting
        self.granularity = granularity
        self.trading_units = trading_units
        self.FeatWindow = FeatWindow
        self.lags = lags

        # get historical data to first fit the the model
        self.data = self.get_history(instrument, train_start, test_end, granularity, price, localize=True)
        self.add_features(lags, features)
        self.train = self.data[train_start:train_end].copy(deep=True)
        self.test = self.data[test_start:test_end].copy(deep=True)
        self.mu = self.train[self.selFeatures].mean()
        self.stdev = self.train[self.selFeatures].std()
        self.train[self.selFeatures] = (self.train[self.selFeatures]-self.mu)/self.stdev
        self.test[self.selFeatures] = (self.test[self.selFeatures]-self.mu)/self.stdev
        self.cv = TimeSeriesSplit(n_splits=5, gap=FeatWindow+lags)  # cross validation to determine model hyperparameters

        # initialise parameters for live trading
        self.position = 0
        self.tick_data = pd.DataFrame()
        self.min_bars = lags + FeatWindow

    def on_success(self, time, bid, ask):
        # 1. collect the tick data
        mid = (bid + ask) / 2
        df = pd.DataFrame({'mid': mid}, index=[pd.Timestamp(time)])
        self.tick_data = pd.concat((self.tick_data, df))

        # 2. resample the tick data
        temp = self.tick_data.resample('1min').ohlc()
        temp.columns = ['o', 'h', 'l', 'c']
        temp.ffill(inplace=True)
        temp.dropna(inplace=True)

        self.live = temp.copy(deep=True)
        self.live['r'] = np.log(self.live['c'] / self.live['c'].shift(1))
        self.live['diff'] = self.live["c"] - self.live["c"].shift()
        self.live['d'] = np.where(self.live['r'] > 0, 1, 0)
        self.live.ffill(inplace=True)
        # self.live.dropna(inplace=True)

        # 3. generate signals/check for trades/place trades
        if len(self.live) > self.min_bars:
            self.min_bars += 1
            X_live = self.ret_features_live()
            signal = self.model.predict(X_live)
            print("signal ", signal)

            if self.position in [0, -1] and signal == 1:
                # go long
                print(f'signal={signal} | going long')
                order = self.create_order(self.stream_instrument,
                                          units=(1 - self.position) * self.trading_units,
                                          ret=True)
                q(signal)
                q(self.live.iloc[-(lags+1):-1])
                q(order)
                self.position = 1
            elif self.position in [0, 1] and signal == 0:
                # go short
                print(f'signal={signal} | going short')
                order = self.create_order(self.stream_instrument,
                                          units=-(1 + self.position) * self.trading_units,
                                          ret=True)
                q(signal)
                q(self.live.iloc[-(lags+1):-1])
                q(order)
                self.position = -1

    def add_features(self, lags, features):
        window = self.FeatWindow
        # reinitialise features table
        self.selFeatures = []
        self.features = []
        colsF = ['c', 'o', 'h', 'l', 'r', 'diff']  # list of features
        colsFL = ['c', 'o', 'h', 'l', 'r', 'diff']  # list of features on which we apply lags

        self.data['diff'] = self.data["c"] - self.data["c"].shift()
        self.data['r'] = self.data["c"] / self.data["c"].shift()-1.
        self.data['d'] = np.where(self.data['r'] > 0, 1, 0)

        if(bool(features)):  # check if the dictionnaire is not empty
            for f in features:
                if(f == "trend"):
                    # https://school.stockcharts.com/doku.php?id=technical_indicators:price_oscillators_ppo
                    # The Percentage Price Oscillator (PPO) is a momentum oscillator that measures the difference between two moving averages as a percentage of the larger moving average.
                    t = ta.momentum.PercentagePriceOscillator(
                        self.data['c'], window_slow=window, window_fast=int(0.5*window), window_sign=int(0.375*window),
                        fillna=False)
                    self.data['trend'] = t.ppo_signal()
                    colsF.append('trend')

                if(f == "rsi"):
                    t = ta.momentum.RSIIndicator(self.data['c'], window=window, fillna=False)
                    self.data['rsi'] = t.rsi()
                    colsF.append('rsi')

                if(f == "sto"):
                    mini = self.data['c'].rolling(window).min()
                    maxi = self.data['c'].rolling(window).max()
                    self.data['sto'] = (self.data['c']-mini)/(maxi-mini)
                    colsF.append('sto')

                if(f == "rev"):
                    # Identify when trends are likely to change direction.
                    t = ta.trend.AroonIndicator(high=self.data['h'], low=self.data['l'], window=window, fillna=False)
                    self.data['rev'] = t.aroon_indicator()
                    colsF.append('rev')

                if(f == "bol"):
                    # Initialize Bollinger Bands Indicator
                    # https://school.stockcharts.com/doku.php?id=technical_indicators:bollinger_band_perce
                    indicator_bb = BollingerBands(close=self.data['c'], window=window, window_dev=2)
                    # Bollinger Channel Percentage Band
                    self.data['bol'] = indicator_bb.bollinger_pband()
                    colsF.append('bol')

                if(f == "minmax"):
                    # minimum and maximum values
                    self.data['min'] = self.data['c'].rolling(window).min()
                    colsF.append('min')
                    self.data['max'] = self.data['c'].rolling(window).max()
                    colsF.append('max')

            for i in colsF:
                col = f'{i}_lag_1'
                self.data[col] = self.data[i].shift(1)
                self.features.append(col)
                self.selFeatures.append(col)

                if i in colsFL:  # we use lags only for colsFL variables
                    for lag in range(2, lags + 1):
                        col = f'{i}_lag_{lag}'
                        self.data[col] = self.data[i].shift(lag)
                        self.features.append(col)
                        self.selFeatures.append(col)

        self.colsF = colsF
        self.colsFL = colsFL
        self.data.ffill(inplace=True)
        self.data.dropna(inplace=True)

    def ret_features_live(self):
        window = self.FeatWindow
        for f in self.colsF:
            if(f == "trend"):
                # https://school.stockcharts.com/doku.php?id=technical_indicators:price_oscillators_ppo
                # The Percentage Price Oscillator (PPO) is a momentum oscillator that measures the difference between two moving averages as a percentage of the larger moving average.
                t = ta.momentum.PercentagePriceOscillator(self.live['c'], window_slow=window, window_fast=int(
                    0.5*window), window_sign=int(0.375*window), fillna=False)
                self.live['trend'] = t.ppo_signal()

            if(f == "rsi"):
                t = ta.momentum.RSIIndicator(self.live['c'], window=window, fillna=False)
                self.live['rsi'] = t.rsi()

            if(f == "sto"):
                mini = self.live['c'].rolling(window).min()
                maxi = self.live['c'].rolling(window).max()
                self.live['sto'] = (self.live['c']-mini)/(maxi-mini)

            if(f == "rev"):
                # Identify when trends are likely to change direction.
                t = ta.trend.AroonIndicator(high=self.live['h'], low=self.live['l'], window=window, fillna=False)
                self.live['rev'] = t.aroon_indicator()

            if(f == "bol"):
                # Initialize Bollinger Bands Indicator
                # https://school.stockcharts.com/doku.php?id=technical_indicators:bollinger_band_perce
                indicator_bb = BollingerBands(close=self.live['c'], window=window, window_dev=2)
                # Bollinger Channel Percentage Band
                self.live['bol'] = indicator_bb.bollinger_pband()

            if(f == "minmax"):
                # minimum and maximum values
                self.live['min'] = self.live['c'].rolling(window).min()
                self.live['max'] = self.live['c'].rolling(window).max()

        for i in self.colsF:
            col = f'{i}_lag_1'
            self.live[col] = self.live[i].shift(0)  # we don't lag in live trading mode
            if i in self.colsFL:  # we use lags only for colsFL variables
                for lag in range(2, lags + 1):
                    col = f'{i}_lag_{lag}'
                    self.live[col] = self.live[i].shift(lag-1)  # we reduce lag by 1

        self.live.ffill(inplace=True)
        # self.live.dropna(inplace=True)
        ret = (self.live[self.selFeatures].iloc[-1]-self.mu)/self.stdev
        ret = pd.DataFrame(ret).T
        return ret

    def fit(self):
        X_train = self.train[self.selFeatures]
        Y_train = self.train['d']

        """
        mlp = BaggingClassifier()
        parameter_space = {
            'n_estimators': [3, 5, 10],
            'max_features': [0.25, 0.5],
            'max_samples': [0.125, 0.25, 0.5]
        }
        clf = GridSearchCV(mlp, parameter_space, n_jobs=-1, cv=self.cv)
        clf.fit(X_train, Y_train)

        # Best paramete set
        print('Best parameters found:\n', clf.best_params_)

        # All results
        means = clf.cv_results_['mean_test_score']
        stds = clf.cv_results_['std_test_score']
        for mean, std, params in zip(means, stds, clf.cv_results_['params']):
            print("%0.3f (+/-%0.03f) for %r" % (mean, std * 2, params))

        """
        nb1 = self.train['d'].sum()
        nb0 = len(self.train['d']) - nb1
        spw = float(nb0/nb1)

        mlp = XGBClassifier()
        params = {
            'min_child_weight': [5, 10, 20],
            'gamma': [0.5, 1, 1.5, 2, 5],
            'subsample': [0.6, 0.8, 1.0],
            'colsample_bytree': [0.6, 0.8, 1.0],
            'max_depth': [3, 4, 5],
            'scale_pos_weight': [spw]
        }

        clf = GridSearchCV(mlp, params, n_jobs=-1, cv=self.cv)
        clf.fit(X_train, Y_train)

        X_test = self.test[self.selFeatures]
        Y_test = self.test['d']

        self.model = clf
        y_pred_test = clf.predict(X_test)
        y_pred_train = clf.predict(X_train)

        self.test['p'] = y_pred_test
        self.train['p'] = y_pred_train

        from sklearn.metrics import classification_report
        print('Results on the train set:')
        print(classification_report(Y_train, y_pred_train))

        print('Results on the test set:')
        print(classification_report(Y_test, y_pred_test))

    def backtest(self, costs=0., sl_stop=None, tp_stop=None):
        # we use VectorBT package to backtest
        dstartTest = self.test.index[0]
        dstartTrain = self.train.index[0]

        print(" TRAIN DATA BAVKTEST")
        # on test data
        p = pd.DataFrame(index=self.train.index)
        p = p.join(self.train["p"])
        p = p.loc[dstartTrain:]
        p["entries"] = np.where(p["p"] == 1, True, False)
        p["short_entries"] = np.where(p["p"] == 0, True, False)
        pf_kwargs = dict(fees=costs, size=self.trading_units, size_type='value', sl_stop=sl_stop, tp_stop=tp_stop)
        pf = vbt.Portfolio.from_signals(self.train.loc[dstartTrain:, 'c'].shift(
        ), entries=p["entries"], short_entries=p["short_entries"], **pf_kwargs)
        pf.orders.count()
        pf.plot().show()
        print(pf.stats())
        print(50*"")

        print(" ON TEST DATA")
        # on test data
        p = pd.DataFrame(index=self.test.index)
        p = p.join(self.test["p"])
        p = p.loc[dstartTest:]
        p["entries"] = np.where(p["p"] == 1, True, False)
        p["short_entries"] = np.where(p["p"] == 0, True, False)
        pf_kwargs = dict(fees=costs, size=self.trading_units, size_type='value', sl_stop=sl_stop, tp_stop=tp_stop)
        pf = vbt.Portfolio.from_signals(self.test.loc[dstartTest:, 'c'].shift(
        ), entries=p["entries"], short_entries=p["short_entries"], **pf_kwargs)
        pf.orders.count()
        pf.plot().show()
        print(pf.stats())

    def live_trade(self):
        print('*** GETTING STARTED STREAMING ***')
        self.stream_data('EUR_USD')

        print('*** CLOSING OUT FINAL POSITION ***')
        order = self.create_order(self.stream_instrument,
                                  units=-self.position * self.trading_units,
                                  ret=True)
        q(order)
        print(self.tick_data.info())




In [ ]:
lags = 5
FeatWindow = 10
features = ["trend", "bol", "rev", "sto"]
#features = ["trend", "bol", "rev"]
algo = AlgoTrader('oanda.cfg', features=features, lags=lags, FeatWindow=FeatWindow, trading_units=100000)

In [ ]:
algo.fit()

Results on the train set:
              precision    recall  f1-score   support

           0       0.62      0.61      0.62      8452
           1       0.54      0.55      0.55      7092

    accuracy                           0.58     15544
   macro avg       0.58      0.58      0.58     15544
weighted avg       0.58      0.58      0.58     15544

Results on the test set:
              precision    recall  f1-score   support

           0       0.55      0.61      0.58      4674
           1       0.47      0.41      0.44      4011

    accuracy                           0.52      8685
   macro avg       0.51      0.51      0.51      8685
weighted avg       0.51      0.52      0.51      8685



In [ ]:
algo.backtest()

 TRAIN DATA BAVKTEST


/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sharpe_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'calmar_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'omega_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sortino_ratio' requires frequency to be set



Start                         2023-11-12 22:18:00
End                           2023-11-24 21:57:00
Period                                      14226
Start Value                                 100.0
End Value                             3205.098277
Total Return [%]                      3105.098277
Benchmark Return [%]                     2.390625
Max Gross Exposure [%]                      100.0
Total Fees Paid                               0.0
Max Drawdown [%]                        65.426453
Max Drawdown Duration                      2293.0
Total Trades                                 5437
Total Closed Trades                          5436
Total Open Trades                               1
Open Trade PnL                                0.0
Win Rate [%]                            58.222958
Best Trade [%]                           0.487641
Worst Trade [%]                         -0.193071
Avg Winning Trade [%]                    0.010306
Avg Losing Trade [%]                     -0.01292


Start                         2023-11-26 22:03:00
End                           2023-12-03 23:59:00
Period                                       7258
Start Value                                 100.0
End Value                              -13.119018
Total Return [%]                      -113.119018
Benchmark Return [%]                    -0.536308
Max Gross Exposure [%]                      100.0
Total Fees Paid                               0.0
Max Drawdown [%]                       106.558919
Max Drawdown Duration                      7079.0
Total Trades                                  304
Total Closed Trades                           303
Total Open Trades                               1
Open Trade PnL                           0.073389
Win Rate [%]                            49.834983
Best Trade [%]                           0.057547
Worst Trade [%]                         -0.067596
Avg Winning Trade [%]                    0.008611
Avg Losing Trade [%]                    -0.010819


/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sharpe_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'calmar_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'omega_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sortino_ratio' requires frequency to be set



In [ ]:
algo.live_trade()

*** GETTING STARTED STREAMING ***


KeyboardInterrupt: ignored